<h1 style="text-align: center; font-size: 50px;"> OpenCellID Exploratory Data Analysis with Panel and cuDF </h1>

This project is a GPU-accelerated, interactive **exploratory data analysis (EDA)** dashboard for the [OpenCellID](https://www.opencellid.org/) dataset. It uses **Panel** and **cuDF** to deliver lightning-fast geospatial analysis and visualization.

You can explore cell tower distributions by radio type, operator, country, and time window — rendered live on an interactive map with full GPU acceleration.

# Notebook Overview
- Start Execution
- Install and Import Libraries
- Configure Settings
- Download Cell Data
- Verify Assets
- Read cell-data
- Read mcc-mnc dataset to map to carrier name
- Analyzing Operator types
- Analyzing Radio types
- Create an exploratory panel dashboard

# Start Execution

In [1]:
import logging  # For application-level logging
import time     # For runtime measurement (wall clock)

# Configure logger
logger: logging.Logger = logging.getLogger("run_workflow_logger")
logger.setLevel(logging.INFO)
logger.propagate = False  # Prevent duplicate logs from parent loggers

# Set formatter
formatter: logging.Formatter = logging.Formatter(
    fmt="%(asctime)s - %(levelname)s - %(message)s",
    datefmt="%Y-%m-%d %H:%M:%S"
)

# Configure and attach stream handler
stream_handler: logging.StreamHandler = logging.StreamHandler()
stream_handler.setFormatter(formatter)
logger.addHandler(stream_handler)

In [2]:
start_time = time.time()  

logger.info("Notebook execution started.")

2025-09-10 16:10:55 - INFO - Notebook execution started.


# Install and Import Libraries

In [3]:
# Install required Python packages listed in requirements.txt silently
%pip install -r ../requirements.txt --quiet

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cuxfilter 25.2.0 requires cupy-cuda11x>=12.0.0, which is not installed.

[notice] A new release of pip is available: 24.3.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [4]:
# Enable GPU-accelerated pandas API via cuDF
%load_ext cudf.pandas

In [5]:
# ------------------------- Standard Library Imports -------------------------

import warnings   # Warning management and filtering
import sys        # System-specific parameters and functions
import os
from pathlib import Path

# Ensure project root is included in Python's module search path
sys.path.append('..') 

# ------------------------- Core Package Imports -------------------------

import pandas as pd                            # DataFrame operations
from src.opencellid_downloader import download_and_extract  # Data acquisition utility

# ------------------------- Visualization & Dashboard Libraries -------------------------

import hvplot.pandas                           # High-level plotting API for pandas/cuDF
import pydeck as pdk                           # WebGL-powered interactive geospatial visualizations
import panel as pn                             # Dashboarding framework for interactive apps
import param                                   # Parameterized configuration support

# Initialize Panel with the required extensions and a material design theme
pn.extension("deckgl", loading_indicator=True, template="material")

# Configure Settings

In [6]:
# ------------------------ Suppress Verbose Logs ------------------------
warnings.filterwarnings("ignore")

In [7]:
# ------------------------- Paths -------------------------
DATA_PATH = '../data/cell_towers_us.csv'
DATA_URL = 'https://s3.amazonaws.com/mcc-mnc.net/mcc-mnc.csv'

# Download Cell Data

### Dataset Options
1. [Worldwide Dataset](https://data.rapids.ai/cudf/datasets/cell_towers.tar.xz) 
2. [US Dataset](https://data.rapids.ai/cudf/datasets/cell_towers_us.tar.xz): Suitable for the free tier of Google Colab.

- Users can register for an account on OpenCellID to obtain a data access token and download the latest dataset directly.
- The auto-downloader provided in this notebook will not fetch the latest dataset from OpenCellID. For the latest data, manual download with an access token is required.
- If the latest data is not a priority, the included dataset dated May 2024 will suffice for exploring the notebook's functionalities.

In [8]:
# Download and extract the OpenCellID dataset for the United States.
# Use download_and_extract('worldwide') to retrieve the full global dataset.
download_and_extract("us")

Download completed: ../data/cell_towers_us.tar.xz
Extracting ../data/cell_towers_us.tar.xz...
Extraction completed: ../data/cell_towers_us.csv


# Verify Assets

In [9]:
# Check whether the Dataset file exists
if Path(DATA_PATH).exists():
    logger.info("The Dataset is properly configured.")
else:
    logger.info(
        "The Dataset is not properly configured. Please check if the Dataset was downloaded"
        "in your project on AI Studio."
    )

2025-09-10 16:12:05 - INFO - The Dataset is properly configured.


# Read cell-data

### Column Descriptions

- **Radio**:	The generation of broadband cellular network technology (Eg. LTE, GSM)

- **MCC**:	Mobile country code. This info is publicly shared by International Telecommunication Union (link)

- **MNC**:	Mobile network code. This info is publicly shared by International Telecommunication Union (link)

- **AREA**:	Location Area Code

- **CELL**:	This is a unique number used to identify each Base transceiver station or sector of BTS

- **Longitude**:	Longitude, is a geographic coordinate that specifies the east-west position of a point on the Earth's surface

- **Latitude**:	Latitude is a geographic coordinate that specifies the north–south position of a point on the Earth's surface.

- **Range**:	Approximate area within which the cell could be. (In meters)

- **Samples**:	Number of measures processed to get a particular data point

- **Changeable=1**:	The location is determined by processing samples

- **Changeable=0**:	The location is directly obtained from the telecom firm

- **Created**:	When a particular cell was first added to database (UNIX timestamp)

- **Updated**:	When a particular cell was last seen (UNIX timestamp)

- **AverageSignal**:	To get the positions of cells, OpenCelliD processes measurements from data contributors. Each measurement includes GPS location of device + Scanned cell identifier (MCC-MNC-LAC-CID) + Other device properties (Signal strength). In this process, signal strength of the device is averaged. Most ‘averageSignal’ values are 0 because OpenCelliD simply didn’t receive signal strength values.


In [10]:
%%time

# Load the US-specific cell tower data into a pandas DataFrame.
# To load the global dataset instead, change the file path to: './opencellid_data/cell_towers.csv'
cell_tower_df = pd.read_csv(DATA_PATH)

# Standardize column names to match expected schema
cell_tower_df.rename(columns={'net': 'MNC', 'mcc': 'MCC'}, inplace=True)

# Display basic information about the dataset
print(f"Dataset loaded with {cell_tower_df.shape[0]:,} rows and {cell_tower_df.shape[1]} columns.")

# Show a preview of the first few rows
cell_tower_df.head()

Dataset loaded with 7,342,373 rows and 14 columns.
CPU times: user 820 ms, sys: 143 ms, total: 963 ms
Wall time: 2.16 s


radio  MCC  MNC   area   cell  unit        lon        lat  range  samples  \
0   GSM  310  260  32192  22568     0 -73.858566  40.898438   1779       12   
1   GSM  310  260  22629  61562     0 -95.876501  41.286475   3367       17   
2   GSM  310  260  51052  44152     0 -71.084538  42.381555   1000       45   
3   GSM  310  260  51051  40311     0 -71.085559  42.381356   1000       52   
4   GSM  310  260   5973  60092     0 -95.570630  29.735371   1000       22   

   changeable     created     updated  averageSignal  
0           1  1459696254  1489125559              0  
1           1  1459810860  1609205988              0  
2           1  1459812328  1633182437              0  
3           1  1459812328  1527695374              0  
4           1  1459692332  1490851584              0

# Read mcc-mnc dataset to map to carrier name

Publicly available dataset: https://mcc-mnc.net/ powered by [simbase](https://www.simbase.com/)

In [11]:
%%time

# Load carrier metadata (MCC-MNC mapping) from the public CSV source
# Only keep relevant columns: MCC, MNC, Country, and Operator
carrier_metadata_df = pd.read_csv(
    DATA_URL,
    sep=';',
    usecols=['MCC', 'MNC', 'Country', 'Operator']
)

# Column 'Operator' is already correctly named — renaming is redundant but included for consistency
carrier_metadata_df.rename(columns={'Operator': 'Operator'}, inplace=True)

# Preview the loaded carrier metadata
carrier_metadata_df.head()

CPU times: user 72.3 ms, sys: 3.93 ms, total: 76.3 ms
Wall time: 1.53 s


MCC  MNC      Country                               Operator
0  901   27    Worldwide                         Monaco Telecom
1  242   99       Norway                             TampNet AS
2  363    2        Aruba                          Digicel Aruba
3  412   40  Afghanistan                  MTN Group Afghanistan
4  412    1  Afghanistan  Afghan Wireless Communication Company

In [12]:
%%time

# Merge tower data with carrier metadata on MCC and MNC codes
# Drop MCC and MNC columns after merge to avoid redundancy
merged_tower_data = cell_tower_df.merge(
    carrier_metadata_df,
    how='inner',
    on=['MCC', 'MNC']
).drop(columns=['MCC', 'MNC'])

# Preview the merged dataset
merged_tower_data.head()

CPU times: user 34.8 ms, sys: 37.9 ms, total: 72.7 ms
Wall time: 98.9 ms


radio   area   cell  unit        lon        lat  range  samples  changeable  \
0   GSM  32192  22568     0 -73.858566  40.898438   1779       12           1   
1   GSM  22629  61562     0 -95.876501  41.286475   3367       17           1   
2   GSM  51052  44152     0 -71.084538  42.381555   1000       45           1   
3   GSM  51051  40311     0 -71.085559  42.381356   1000       52           1   
4   GSM   5973  60092     0 -95.570630  29.735371   1000       22           1   

      created     updated  averageSignal                   Country  \
0  1459696254  1489125559              0  United States of America   
1  1459810860  1609205988              0  United States of America   
2  1459812328  1633182437              0  United States of America   
3  1459812328  1527695374              0  United States of America   
4  1459692332  1490851584              0  United States of America   

       Operator  
0  T-Mobile USA  
1  T-Mobile USA  
2  T-Mobile USA  
3  T-Mobile USA  
4  T-Mobile USA

# Analyzing Operator types

In [13]:
%%time

# Compute the count of cell towers reported by each operator
operator_tower_counts = merged_tower_data['Operator'].value_counts()

# Display the result
operator_tower_counts

CPU times: user 35.1 ms, sys: 9.41 ms, total: 44.5 ms
Wall time: 83 ms


Operator
T-Mobile USA                         2438095
AT&T Mobility                        2256562
Sprint Corporation                   1486370
Verizon Wireless                      981488
U.S. Cellular                          72391
                                      ...   
Iowa RSA No. 2 LP                          1
LigTel Communications                      1
Mark Twain Communications Company          1
New Dimension Wireless Ltd.                1
Tyntec Inc.                                1
Name: count, Length: 121, dtype: int64

In [14]:
%%time

# Identify operators with fewer than or equal to 1,000 reported cell towers
low_frequency_operators = merged_tower_data['Operator'].value_counts()
low_count_operator_list = low_frequency_operators[low_frequency_operators <= 1000].index.tolist()

# Display the number of such operators
len(low_count_operator_list)

CPU times: user 25 ms, sys: 521 μs, total: 25.5 ms
Wall time: 40 ms


86

In [15]:
%%time

# Replace all low-frequency operators with the label "Other" to simplify visualizations
merged_tower_data['Operator'] = merged_tower_data['Operator'].replace(low_count_operator_list, 'Other')

CPU times: user 22.7 ms, sys: 9.16 ms, total: 31.9 ms
Wall time: 45.7 ms


In [16]:
# Aggregate the number of cell towers per operator by country
operator_distribution_df = merged_tower_data.groupby(['Country', 'Operator'])['radio'].count().reset_index()

# Display the resulting operator distribution DataFrame
operator_distribution_df.head()

Country                Operator  radio
0  American Samoa (USA)                   Other      1
1            Guam (USA)      IT&E Overseas, Inc   1863
2            Guam (USA)      NTT DoCoMo Pacific   2379
3            Guam (USA)  Teleguam Holdings, LLC    722
4            Guam (USA)         Wave Runner LLC    927

# Analyzing Radio types

In [17]:
# Generate a horizontal bar chart to visualize the distribution of radio cell tower types
radio_type_distribution_plot = pn.pane.HoloViews(
    merged_tower_data['radio']
    .value_counts()
    .reset_index()
    .hvplot.barh(
        x='radio',
        y='count',
        xlabel='Radio Type',
        ylabel='Number of Towers',
        title='Distribution of Cell Towers by Radio Type',
        height=400,
        width=600,
        responsive=True,
        tools=['hover']
    ).opts(default_tools=[])
)

# Display the plot
radio_type_distribution_plot

HoloViews(Bars, height=400, sizing_mode='fixed', width=600)

In [18]:
# Generate a horizontal bar chart showing the top 10 countries with the most LTE cell towers
top_lte_countries_plot = pn.pane.HoloViews(
    merged_tower_data[merged_tower_data['radio'] == 'LTE']
    .Country
    .value_counts()
    .reset_index()
    .head(10)
    .hvplot.barh(
        x='Country',
        y='count',
        xlabel='Country',
        ylabel='Number of LTE Towers',
        title='Top 10 Countries by LTE Cell Tower Count',
        height=400,
        width=600,
        responsive=True,
        tools=['hover']
    ).opts(default_tools=[])
)

# Display the plot
top_lte_countries_plot

HoloViews(Bars, height=400, sizing_mode='fixed', width=600)

In [19]:
%%time

# Define the subset of columns to retain for analysis and visualization
selected_columns = [
    'radio', 
    'area', 
    'lon', 
    'lat', 
    'range', 
    'samples', 
    'changeable', 
    'created', 
    'averageSignal', 
    'Country', 
    'Operator'
]

# Filter the merged dataset to keep only the selected columns
merged_tower_data = merged_tower_data[selected_columns]

CPU times: user 417 μs, sys: 40 μs, total: 457 μs
Wall time: 461 μs


# Create an exploratory panel dashboard

In [20]:
%%time

# Define RGBA color mappings for each radio type to enhance dashboard visualizations
radio_color_mapping = {
    'UMTS': [255, 165, 0, 140],    # Orange
    'LTE': [255, 0, 0, 140],       # Red
    'GSM': [135, 206, 250, 140],   # Light Blue
    'CDMA': [123, 104, 238, 140],  # Medium Slate Blue
    'NR': [0, 128, 0, 140]         # Green
}

# Map each radio type to its corresponding RGBA color
merged_tower_data['color'] = merged_tower_data['radio'].map(radio_color_mapping)

# Convert the 'created' UNIX timestamp to a datetime year for easier filtering and visualization
merged_tower_data['created'] = pd.to_datetime(merged_tower_data['created'], unit='s').dt.year

CPU times: user 272 ms, sys: 10.1 ms, total: 282 ms
Wall time: 294 ms


In [21]:
# Define the radio type legend as Markdown for display in the dashboard
radio_type_legend_markdown = """
### Radio Type Legend

- **UMTS**: <span style="height: 10px; width: 10px; background-color: rgba(255, 165, 0, 0.55); border-radius: 50%; display: inline-block;"></span>
- **LTE**: <span style="height: 10px; width: 10px; background-color: rgba(255, 0, 0, 0.55); border-radius: 50%; display: inline-block;"></span>
- **GSM**: <span style="height: 10px; width: 10px; background-color: rgba(135, 206, 250, 0.55); border-radius: 50%; display: inline-block;"></span>
- **CDMA**: <span style="height: 10px; width: 10px; background-color: rgba(123, 104, 238, 0.55); border-radius: 50%; display: inline-block;"></span>
- **NR**: <span style="height: 10px; width: 10px; background-color: rgba(0, 128, 0, 0.55); border-radius: 50%; display: inline-block;"></span>
"""

In [22]:
# Define an interactive dashboard class for visualizing cell tower data
class CellTowerDashboard(param.Parameterized):
    # ---------------- Filter Parameters ----------------
    
    # Radio technology types (e.g., GSM, LTE, UMTS, CDMA, NR)
    radio_type = param.ListSelector(
        objects=merged_tower_data['radio'].unique().tolist(),
        default=[]
    )

    # Mobile network operators (e.g., T-Mobile, AT&T)
    operator = param.ListSelector(
        objects=merged_tower_data['Operator'].value_counts().sort_values(ascending=False).index.tolist(),
        default=[]
    )

    # Country selection
    country = param.ListSelector(
        objects=merged_tower_data['Country'].value_counts().sort_values(ascending=False).index.tolist(),
        default=[]
    )

    # Date range when towers were first reported
    date_range = param.Range(
        bounds=(merged_tower_data['created'].min(), merged_tower_data['created'].max()),
        step=1,
        default=(merged_tower_data['created'].min(), merged_tower_data['created'].max())
    )

    # ---------------- Dashboard State Parameters ----------------

    # Track compute progress for feedback during filtering
    compute_progress = param.Integer(default=0, bounds=(0, 100))

    # Maximum number of points to render for responsiveness
    point_budget = param.Integer(default=50_000, bounds=(10_000, 100_000), step=10_000)

    # Selected data size after filtering
    selected_data_size = param.Integer(default=merged_tower_data.shape[0])

    # Filtered DataFrame to be visualized
    df = param.DataFrame(default=merged_tower_data.sample(50_000))

    # Execution time for filtering operations
    execution_time = param.Number(default=0, doc="Execution Time (seconds)")

    # ---------------- Core Methods ----------------

    @param.depends('radio_type', 'operator', 'country', 'date_range', 'point_budget', watch=True)
    def filter_dataframe(self) -> None:
        """Apply user-selected filters to the dataset and update the displayed DataFrame."""
        start_time = time.time()
        self.compute_progress = 0

        # Apply date range filter
        filtered_indices = merged_tower_data['created'].between(self.date_range[0], self.date_range[1])
        self.compute_progress = 25

        # Apply radio type filter
        if self.radio_type:
            filtered_indices &= merged_tower_data['radio'].isin(self.radio_type)
        self.compute_progress = 50

        # Apply operator filter
        if self.operator:
            filtered_indices &= merged_tower_data['Operator'].isin(self.operator)
        self.compute_progress = 75

        # Apply country filter
        if self.country:
            filtered_indices &= merged_tower_data['Country'].isin(self.country)
        self.compute_progress = 100

        # Final filtered DataFrame
        filtered_df = merged_tower_data[filtered_indices]
        self.selected_data_size = filtered_df.shape[0]

        # Sample data if exceeding point budget
        if filtered_df.shape[0] > self.point_budget:
            filtered_df = filtered_df.sample(n=self.point_budget)

        self.df = filtered_df
        self.execution_time = time.time() - start_time

    @param.depends('df')
    def update_scatter_plot(self) -> pn.Column:
        """Render a 3D scatter plot of the filtered cell towers."""
        base_map_url = "https://d2ad6b4ur7yvpq.cloudfront.net/naturalearth-3.3.0/ne_50m_admin_0_scale_rank.geojson"

        layers = [
            pdk.Layer(
                "GeoJsonLayer",
                id="base-map",
                data=base_map_url,
                stroked=False,
                filled=True,
                get_fill_color=[200, 200, 200],
            ),
            pdk.Layer(
                "ScatterplotLayer",
                self.df,
                pickable=True,
                opacity=0.8,
                stroked=True,
                filled=True,
                radius_scale=6,
                radius_min_pixels=1,
                radius_max_pixels=10,
                line_width_min_pixels=1,
                get_position=["lon", "lat"],
                radius=1000,
                get_line_color="color"
            )
        ]

        view_state = pdk.ViewState(
            latitude=self.df['lat'].median(),
            longitude=self.df['lon'].median(),
            zoom=0,
            bearing=0,
            pitch=0
        )

        view = pdk.View(type="_GlobeView", controller=True)

        return pn.Column(
            "### Visualized Data Points",
            self.visualized_data_size,
            pn.pane.DeckGL(pdk.Deck(views=[view], layers=layers, initial_view_state=view_state, map_provider=None))
        )

    @param.depends('selected_data_size')
    def computed_data_size(self) -> pn.widgets.Number:
        """Display the number of data points after filtering."""
        return pn.widgets.Number(value=self.selected_data_size, format="{value:,}", font_size='25pt')

    @param.depends('execution_time')
    def execution_time_display(self) -> pn.pane.Markdown:
        """Display the compute time for filtering operations."""
        return pn.pane.Markdown(f"### Compute Time: {self.execution_time:.2f} seconds")

    @param.depends('point_budget', 'selected_data_size')
    def visualized_data_size(self) -> pn.widgets.Number:
        """Display the number of points being visualized."""
        points_to_render = min(self.selected_data_size, self.point_budget)
        return pn.widgets.Number(value=points_to_render, format="{value:,}", font_size='15pt')

    @param.depends('df')
    def update_bar_charts(self) -> pn.Column:
        """Generate bar charts for radio type and operator distributions."""
        radio_type_chart = self.df['radio'].value_counts().head().hvplot.barh(
            title="Radio Type Count",
            responsive=True,
            tools=["hover"]
        ).opts(default_tools=[])

        operator_chart = self.df['Operator'].value_counts().head().hvplot.barh(
            title="Operator Tower Count",
            responsive=True,
            tools=["hover"]
        ).opts(default_tools=[])

        return pn.Column(radio_type_chart, operator_chart)

    @param.depends('compute_progress', 'execution_time')
    def compute_progress_bar(self) -> pn.widgets.Progress:
        """Display a progress bar tracking the filtering computation."""
        return pn.widgets.Progress(value=self.compute_progress, active=False, sizing_mode="stretch_width")

    @param.depends('df')
    def view(self) -> pn.GridSpec:
        """Assemble and display the complete interactive dashboard layout."""
        layout = pn.GridSpec(ncols=5, width=1400, height=600)

        # Left Sidebar - Filters and Data Summary
        controls = pn.Column(
            pn.WidgetBox(
                "### Queried Data Points",
                self.computed_data_size,
                pn.Column(
                    pn.Row(
                        self.execution_time_display,
                        pn.widgets.TooltipIcon(
                            value="While rendering is consistent between pandas and cuDF, "
                                  "this dashboard highlights the compute time improvement with cuDF."
                        )
                    ),
                    self.compute_progress_bar
                ),
                sizing_mode="stretch_width"
            ),
            pn.WidgetBox(
                "### Query Filters",
                pn.Param(self.param.radio_type, widgets={"radio_type": {"type": pn.widgets.MultiChoice, "sizing_mode": "stretch_width"}}),
                pn.Param(self.param.operator, widgets={"operator": {"type": pn.widgets.MultiChoice, "sizing_mode": "stretch_width"}}),
                pn.Param(self.param.country, widgets={"country": {"type": pn.widgets.MultiChoice, "sizing_mode": "stretch_width"}}),
                pn.Param(self.param.date_range, widgets={"date_range": {"type": pn.widgets.RangeSlider, "throttled": True, "sizing_mode": "stretch_width"}}),
                pn.Param(self.param.point_budget, widgets={"point_budget": {"type": pn.widgets.IntSlider, "throttled": True, "sizing_mode": "stretch_width"}}),
                sizing_mode="stretch_width"
            )
        )

        # Populate layout
        layout[:, 0] = controls
        layout[:, 1:3] = self.update_scatter_plot
        layout[:, 3:5] = self.update_bar_charts

        return layout

In [23]:
# Instantiate the CellTowerDashboard with an initial point budget for rendering
cell_tower_dashboard = CellTowerDashboard(point_budget=10_000)

# Render and display the interactive dashboard
cell_tower_dashboard.view()

GridSpec(height=600, ncols=5, nrows=1, sizing_mode='fixed', width=1400)
    [0] Column(height=600, width=280)
        [0] WidgetBox(sizing_mode='stretch_width')
            [0] Markdown(str)
            [1] ParamMethod(method, _pane=Number, defer_load=False)
            [2] Column
                [0] Row
                    [0] ParamMethod(method, _pane=Markdown, defer_load=False)
                    [1] TooltipIcon(value='While rendering is consis...)
                [1] ParamMethod(method, _pane=Progress, defer_load=False)
        [1] WidgetBox(sizing_mode='stretch_width')
            [0] Markdown(str)
            [1] Param(CellTowerDashboard, parameters=['radio_type'], show_name=False, widgets={'radio_type': {'type': <c...})
            [2] Param(CellTowerDashboard, parameters=['operator'], show_name=False, widgets={'operator': {'type': <cla...})
            [3] Param(CellTowerDashboard, parameters=['country'], show_name=False, widgets={'country': {'type': <clas...})
            [4] Param(CellTowerDashboard, parameters=['date_range'], show_name=False, widgets={'date_range': {'type': <c...})
            [5] Param(CellTowerDashboard, parameters=['point_budget'], show_name=False, widgets={'point_budget': {'type': ...})
    [1] ParamMethod(method, _pane=Column, defer_load=False, height=600, width=560)
    [2] ParamMethod(method, _pane=Column, defer_load=False, height=600, width=560)

In [24]:
end_time: float = time.time()
elapsed_time: float = end_time - start_time
elapsed_minutes: int = int(elapsed_time // 60)
elapsed_seconds: float = elapsed_time % 60

logger.info(f"⏱️ Total execution time: {elapsed_minutes}m {elapsed_seconds:.2f}s")
logger.info("✅ Notebook execution completed successfully.")

2025-09-10 16:12:15 - INFO - ⏱️ Total execution time: 1m 20.42s
2025-09-10 16:12:15 - INFO - ✅ Notebook execution completed successfully.


Built with ❤️ using Z by HP AI Studio.